In [2]:
!pip install -q transformers sentence_transformers faiss-cpu torch PyPDF2 nltk

In [3]:
!pip install -U langchain-community
from langchain.vectorstores import Qdrant
from langchain.embeddings import HuggingFaceBgeEmbeddings
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.document_loaders import PyPDFDirectoryLoader,TextLoader

In [4]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
from sentence_transformers import SentenceTransformer
!pip install faiss-cpu
!pip install sentence-transformers
import faiss
import numpy as np
import pandas as pd
!
import PyPDF2
import os
import nltk
# nltk.download('punkt')
nltk.download('punkt_tab')
from nltk.tokenize import sent_tokenize
from google.colab import userdata

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


In [5]:
HUGGING_FACE_ACCESS_TOKEN = userdata.get('HF_TOKEN_Z')

model_name = 'google/gemma-2-2b-it'

model = AutoModelForCausalLM.from_pretrained(
    model_name,
    torch_dtype=torch.float16,
    token=HUGGING_FACE_ACCESS_TOKEN
    ).to('cuda')

tokenizer = AutoTokenizer.from_pretrained(model_name, token=HUGGING_FACE_ACCESS_TOKEN)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [6]:
def extract_text_from_pdf(pdf_path):
    try:
        with open(pdf_path, 'rb') as file:
            reader = PyPDF2.PdfReader(file)
            text = "".join([page.extract_text() for page in reader.pages])
        return text
    except Exception as e:
        print(f"Error reading {pdf_path}: {e}")
        return ""

def split_text_into_chunks(text, max_chunk_size=1000):
    sentences = sent_tokenize(text)
    chunks = []
    current_chunk = ""

    for sentence in sentences:
        if len(current_chunk) + len(sentence) <= max_chunk_size:
            current_chunk += sentence + " "
        else:
            chunks.append(current_chunk.strip())
            current_chunk = sentence + " "

    if current_chunk:
        chunks.append(current_chunk.strip())

    return chunks

In [7]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [8]:
# check list pdfs and replace with yourpath

os.chdir('/content/drive/MyDrive/Data')
!ls

data_cleaned_aisc.pdf


In [9]:
encoder = SentenceTransformer('all-MiniLM-L6-v2')

# Process PDF files
pdf_directory = "/content/drive/MyDrive/Data"
df_documents = pd.DataFrame(columns=['path', 'text_chunks', 'embeddings'])

for filename in os.listdir(pdf_directory):
    if filename.endswith(".pdf"):
        print(filename)
        pdf_path = os.path.join(pdf_directory, filename)
        text = extract_text_from_pdf(pdf_path)
        chunks = split_text_into_chunks(text)
        document_embeddings = encoder.encode(chunks)
        new_row = pd.DataFrame({'path': [pdf_path], 'text_chunks': [chunks], 'embeddings': [document_embeddings]})
        df_documents = pd.concat([df_documents, new_row], ignore_index=True)

df_documents

data_cleaned_aisc.pdf


path  \
0  /content/drive/MyDrive/Data/data_cleaned_aisc.pdf   

                                         text_chunks  \
0  [Keo - Pad tản nhiệt là gì? Keo - Pad tản nhiệ...   

                                          embeddings  
0  [[0.0036073995, -0.059478104, 0.06371901, -0.0...

In [10]:
all_embeddings = np.vstack(df_documents['embeddings'].tolist())
dimension = all_embeddings.shape[1]
index = faiss.IndexFlatL2(dimension)
index.add(all_embeddings)

In [11]:
def find_most_similar_chunks(query, top_k=3):
    query_embedding = encoder.encode([query])
    distances, indices = index.search(query_embedding, top_k)
    results = []
    total_chunks = sum(len(chunks) for chunks in df_documents['text_chunks'])
    for i, idx in enumerate(indices[0]):
        if idx < total_chunks:
            doc_idx = 0
            chunk_idx = idx
            while chunk_idx >= len(df_documents['text_chunks'].iloc[doc_idx]):
                chunk_idx -= len(df_documents['text_chunks'].iloc[doc_idx])
                doc_idx += 1
            results.append({
                'document': df_documents['path'].iloc[doc_idx],
                'chunk': df_documents['text_chunks'].iloc[doc_idx][chunk_idx],
                'distance': distances[0][i]
            })
    return results

def generate_response(query, context, max_length=1000):
    # query_template = "Bạn là một chatbot tư vấn khách hàng. Hãy trả lời câu hỏi sau dựa trên ngữ cảnh, nếu ngữ cảnh không cung cấp câu trả lời hoặc không chắc chắn hãy trả lời 'Tôi không biết thông tin này, tuy nhiên đoạn thông tin dưới phần tham khảo có thể có câu trả lời cho bạn!' đừng cố tạo ra câu trả lời không có trong ngữ cảnh.\nNgữ cảnh: {context} \nCâu hỏi: {question}\nTrả lời: "
    # query_template = "Tham khảo ngữ cảnh:{context}\n\n### Câu hỏi:{question}\n\n### Trả lời:"
    prompt = f"Context: {context}\n\nQuestion: {query}\n\nAnswer:"
    input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to('cuda')

    with torch.no_grad():
        output = model.generate(input_ids, max_new_tokens=max_length, num_return_sequences=1)

    decoded_output = tokenizer.decode(output[0], skip_special_tokens=True)

    # Extracting the answer part by removing the prompt portion
    answer_start = decoded_output.find("Answer:") + len("Answer:")
    answer = decoded_output[answer_start:].strip()

    return answer

def query_documents(query):
    similar_chunks = find_most_similar_chunks(query)
    context = " ".join([result['chunk'].replace("\n", "") for result in similar_chunks])
    response = generate_response(query, context)
    return response, similar_chunks

In [12]:
query = "Keo-Pad tản nhiệt là gì?"
answer, relevant_chunks = query_documents(query)

print(f"Query: {query}\n\n-----\n")
print(f"Generated answer: {answer}\n\n-----\n")
print("Relevant chunks:")
for chunk in relevant_chunks:
    print(f"Document: {chunk['document']}")
    print(f"Chunk: {chunk['chunk']}".replace("\n", ""))
    print(f"Distance: {chunk['distance']}")
    print()

Query: Keo-Pad tản nhiệt là gì?

-----

Generated answer: Keo-Pad tản nhiệt là một loại vật liệu được sử dụng để lấp đầy khoảng hở giữa bộ xử lý và bộ tản nhiệt, giúp cải thiện khả năng truy ền nhiệt từ bộ xử lý đến bộ tản nhiệt, từ đó giúp giảm nhiệt độ của bộ xử lý.

-----

Relevant chunks:
Document: /content/drive/MyDrive/Data/data_cleaned_aisc.pdf
Chunk: Có nhiều loại keo - pad tản nhiệt khác nhau trên th ị trường, bao g ồm keo - pad tản nhiệt silicon, keo - pad tản nhiệt carbon, keo - pad tản nhiệt kim loại lỏng và keo - pad tản nhiệt silicon ceramic. Keo - pad tản nhiệt silicon là gì? Keo - Pad tản nhiệt silicon là m ột loại keo - pad tản nhiệt được làm từ silicon, có đ ộ bền cao, khả năng dẫn nhiệt tốt và giá thành h ợp lý. Keo - pad tản nhiệt carbon là gì? Keo - Pad tản nhiệt carbon là m ột loại keo - pad tản nhiệt được làm từ carbon, có kh ả năng dẫn nhiệt tốt và độ bền cao, nhưng giá thành tương đ ối cao. Keo - pad tản nhiệt kim loại lỏng là gì? Keo - Pad tản nhiệt kim loại l

In [13]:
query = "Tôi muốn quần áo mặc cho mùa đông cho trẻ em"
answer, relevant_chunks = query_documents(query)

print(f"Query: {query}\n\n-----\n")
print(f"Generated answer: {answer}\n\n-----\n")
print("Relevant chunks:")
for chunk in relevant_chunks:
    print(f"Document: {chunk['document']}")
    print(f"Chunk: {chunk['chunk']}".replace("\n", ""))
    print(f"Distance: {chunk['distance']}")
    print()

Query: Tôi muốn quần áo mặc cho mùa đông cho trẻ em

-----

Generated answer: Bạn muốn tìm quần áo mùa đông cho trẻ em, vậy nên cần lưu ý những điều sau:

**1. Chất liệu:** 
   - Chọn quần áo làm từ chất liệu ấm áp, giữ nhiệt tốt như: Fleece, Thicken Wool, Cotton, Flannel.
   -  Kiểm tra xem chất liệu có mềm mại, dễ chịu cho trẻ không.

**2. Thiết kế:** 
   -  Tùy theo độ tuổi và sở thích của trẻ, lựa chọn quần áo có thiết kế phù hợp. 
   -  Kiểm tra xem quần áo có đủ các lớp để giữ ấm, tránh bị lạnh.

**3. Độ bền:** 
   -  Chọn quần áo có độ bền cao, dễ dàng giặt sạch. 
   -  Kiểm tra xem quần áo có đường may chắc chắn, khóa kéo và phụ kiện tốt.

**4. Màu sắc:** 
   -  Lựa chọn màu sắc phù hợp với sở thích của trẻ. 
   -  Màu sắc tươi sáng, dễ nhìn sẽ giúp trẻ cảm thấy vui vẻ.

**5. Giá cả:** 
   -  Lựa chọn quần áo phù hợp với ngân sách của gia đình. 
   -  Lưu ý giá cả có thể thay đổi tùy theo thương hiệu và chất liệu.

**6. Thương hiệu:** 
   -  Lựa chọn thương hiệu uy tín, có chất

In [14]:
query = "Chủ tịch Hồ Chí Minh là ai?"
answer, relevant_chunks = query_documents(query)

print(f"Query: {query}\n\n-----\n")
print(f"Generated answer: {answer}\n\n-----\n")
print("Relevant chunks:")
for chunk in relevant_chunks:
    print(f"Document: {chunk['document']}")
    print(f"Chunk: {chunk['chunk']}".replace("\n", ""))
    print(f"Distance: {chunk['distance']}")
    print()

Query: Chủ tịch Hồ Chí Minh là ai?

-----

Generated answer: Chủ tịch Hồ Chí Minh là một nhà cách mạng, chính trị gia, và nhà văn Việt Nam.

-----

Relevant chunks:
Document: /content/drive/MyDrive/Data/data_cleaned_aisc.pdf
Chunk: ', '' '', '' 'M ột số thương hi ệu đồng hồ trẻ em được đánh giá cao bao g ồm Casio, Citizen, Seiko, Timex, Daniel Wellington, Skmei, APELA, Olympia Star,...', '' '', '' 'Có đ ồng hồ trẻ em nào có th ể sử dụng cho trẻ nhỏ từ 2-3 tuổi không? ', '' '', '' 'Có, m ột số thương hi ệu đồng hồ trẻ em có sản xuất đồng hồ dành riêng cho trẻ nhỏ từ 2-3 tuổi với thiết kế đơn giản, dây đeo m ềm mại. ', '' '', '' 'M ột chiếc đồng hồ thông minh dành cho tr ẻ em có nh ững tính năng h ữu ích nào? ', '' '', '' 'Đ ồng hồ thông minh dành cho tr ẻ em thường có các tính năng như g ọi điện, nhắn tin, định vị GPS, theo dõi hoạt động, chơi trò chơi, k ết nối với thiết bị di động,... giúp ph ụ huynh có th ể quản lý và giám sát tr ẻ dễ dàng hơn. ', '' '', '' 'Đ ồng hồ trẻ em nên có m 

In [15]:
!pip install flask flask-ngrok

In [18]:
!pip install pyngrok

In [21]:
!pip install gradio

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.2/57.2 MB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.2/320.2 kB 25.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 94.8/94.8 kB 9.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.2/11.2 MB 68.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.2/73.2 kB 8.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.8/63.8 kB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.2/168.2 kB 17.8 MB/s eta 0:00:00
  Attempting uninstall: markupsafe
    Found existing installation: MarkupSafe 3.0.2
    Uninstalling MarkupSafe-3.0.2:
      Successfully uninstalled MarkupSafe-3.0.2
